# app

> Gradio app.py

In [ ]:
#| default_exp app

In [ ]:
#| hide
from nbdev.showdoc import *

In [ ]:
#| export
import copy
import os

import gradio as gr
from fastcore.utils import in_jupyter
from langchain.chains import ConversationChain
from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.prompts.chat import (
    ChatPromptTemplate,
    HumanMessagePromptTemplate,
    MessagesPlaceholder,
)
from PIL import Image

import constants
from lv_recipe_chatbot.engineer_prompt import INIT_PROMPT
from lv_recipe_chatbot.ingredient_vision import (
    SAMPLE_IMG_DIR,
    BlipImageCaptioning,
    VeganIngredientFinder,
    format_image,
)

In [ ]:
# | export


class ConversationBot:
    def __init__(self, verbose=True):
        self.chat = ChatOpenAI(temperature=1, verbose=True)
        self.memory = ConversationBufferMemory(return_messages=True)
        self.init_prompt = copy.deepcopy(INIT_PROMPT)
        init_prompt_msgs = self.init_prompt.messages
        self.ai_prompt_questions = {
            "ingredients": init_prompt_msgs[1],
            "allergies": init_prompt_msgs[3],
            "recipe_open_params": init_prompt_msgs[5],
        }
        self.img_cap = BlipImageCaptioning("cpu")
        self.vegan_ingred_finder = VeganIngredientFinder()
        self.verbose = verbose

    def respond(self, user_msg, chat_history):
        response = self._get_bot_response(user_msg, chat_history)
        chat_history.append((user_msg, response))
        return "", chat_history

    def init_conversation(self, formatted_chat_prompt):
        self.conversation = ConversationChain(
            llm=self.chat,
            memory=self.memory,
            prompt=formatted_chat_prompt,
            verbose=self.verbose,
        )

    def reset(self):
        self.memory.clear()
        self.init_prompt = copy.deepcopy(INIT_PROMPT)

    def run_img(self, image: str):
        desc = self.img_cap.inference(format_image(image))
        answer = self.vegan_ingred_finder.list_ingredients(image)
        msg = f"""I uploaded an image that may contain vegan ingredients.
The description of the image is: `{desc}`.
The extracted ingredients are:
```
{answer}
```
"""
        base_prompt = INIT_PROMPT.messages[2].prompt.template
        new_prompt = f"{msg}I may type some more ingredients below.\n{base_prompt}"
        self.init_prompt.messages[2].prompt.template = new_prompt
        return msg

    def _get_bot_response(self, user_msg: str, chat_history) -> str:
        if len(chat_history) < 2:
            return self.ai_prompt_questions["allergies"].prompt.template

        if len(chat_history) < 3:
            return self.ai_prompt_questions["recipe_open_params"].prompt.template

        if len(chat_history) < 4:
            user = 0
            ai = 1
            user_msgs = [msg_pair[user] for msg_pair in chat_history[1:]]
            f_init_prompt = self.init_prompt.format_prompt(
                ingredients=user_msgs[0],
                allergies=user_msgs[1],
                recipe_freeform_input=user_msg,
            )
            chat_msgs = f_init_prompt.to_messages()
            results = self.chat.generate([chat_msgs])
            chat_msgs.extend(
                [
                    results.generations[0][0].message,
                    MessagesPlaceholder(variable_name="history"),
                    HumanMessagePromptTemplate.from_template("{input}"),
                ]
            )
            open_prompt = ChatPromptTemplate.from_messages(chat_msgs)
            # prepare the open conversation chain from this point
            self.init_conversation(open_prompt)
            return results.generations[0][0].message.content

        response = self.conversation.predict(input=user_msg)
        return response

    def __del__(self):
        del self.vegan_ingred_finder

In [ ]:
os.listdir(SAMPLE_IMG_DIR)
SAMPLE_IMG_DIR

Path('/home/evylz/AnimalEquality/lv-recipe-chatbot/assets/images/vegan_ingredients')

In [ ]:
from dotenv import load_dotenv

In [ ]:
load_dotenv()

True

In [ ]:
%time bot = ConversationBot()

CPU times: user 6.19 s, sys: 1.47 s, total: 7.66 s
Wall time: 4.68 s


In [ ]:
%time print(bot.run_img(SAMPLE_IMG_DIR / "veggie-fridge.jpeg"))

I uploaded an image that may contain vegan ingredients.
The description of the image is: `a refrigerator with food inside`.
The extracted ingredients are:
```
cabbage lettuce onion
apples
rice
plant-based milk
```

CPU times: user 56.7 s, sys: 63.6 ms, total: 56.8 s
Wall time: 5.95 s


In [ ]:
bot.init_prompt.messages[2]

HumanMessagePromptTemplate(prompt=PromptTemplate(input_variables=['ingredients'], output_parser=None, partial_variables={}, template='I uploaded an image that may contain vegan ingredients.\nThe description of the image is: `a refrigerator with food inside`.\nThe extracted ingredients are:\n```\ncabbage lettuce onion\napples\nrice\nplant-based milk\n```\nI may type some more ingredients below.\nIngredients: {ingredients}', template_format='f-string', validate_template=True), additional_kwargs={})

In [ ]:
INIT_PROMPT.messages[2]

HumanMessagePromptTemplate(prompt=PromptTemplate(input_variables=['ingredients'], output_parser=None, partial_variables={}, template='Ingredients: {ingredients}', template_format='f-string', validate_template=True), additional_kwargs={})

In [ ]:
#| export


def create_demo(bot=ConversationBot):
    sample_images = []
    all_imgs = [f"{SAMPLE_IMG_DIR}/{img}" for img in os.listdir(SAMPLE_IMG_DIR)]
    for i, img in enumerate(all_imgs):
        if i in [
            1,
            2,
            3,
        ]:
            sample_images.append(img)
    with gr.Blocks() as demo:
        gr_img = gr.Image(type="filepath")
        btn = gr.Button(value="Submit image")
        ingredients_msg = gr.Text(label="Ingredients from image")
        btn.click(bot.run_img, inputs=[gr_img], outputs=[ingredients_msg])
        gr.Examples(
            examples=sample_images,
            inputs=gr_img,
        )

        chatbot = gr.Chatbot(
            value=[(None, bot.ai_prompt_questions["ingredients"].prompt.template)]
        )

        msg = gr.Textbox()
        # clear = gr.Button("Clear")
        gr.Markdown("**🔃Refresh the page to start from scratch🔃**")

        msg.submit(
            fn=bot.respond, inputs=[msg, chatbot], outputs=[msg, chatbot], queue=False
        )
        # clear.click(lambda: None, None, chatbot, queue=False).then(bot.reset)
        return demo

In [ ]:
if "demo" in globals():
    demo.close()
demo = create_demo(bot)
demo.launch()

Closing server running on port: 7860
Running on local URL:  http://127.0.0.1:7860

To create a public link, set `share=True` in `launch()`.


In [ ]:
#| hide
import nbdev

nbdev.nbdev_export()